In [1]:
%load_ext jupyter_black

In [2]:
import spotipy
from spotipy.oauth2 import SpotifyOAuth
import os
import sys
import pandas as pd
import numpy as np
import requests
from spotify_dl import spotify_dl
from pathlib import Path
import time
import os
from dotenv import load_dotenv  # changed magic command to explicit load
import librosa
import matplotlib.pyplot as plt
from datetime import datetime
from sklearn.metrics import pairwise
from sklearn.model_selection import train_test_split
from typing import List
from flask import Flask, redirect, request
import random
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv2D  # new
from tensorflow.keras.layers import MaxPooling2D  # new
from tensorflow.keras.layers import Flatten  # new
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout
from tensorflow.keras.applications import ResNet50V2
from tensorflow.keras.callbacks import EarlyStopping
from skimage.transform import resize


pd.set_option("display.max_rows", None)  # pandas dataframe formatting options
pd.set_option("display.max_columns", None)


custom_env_path = "../../brainstation_capstone_cfg.env"  # environment variables file

## Read in Kaggle Dataset

In [3]:
kaggle_df = pd.read_csv("../data/SpotifyFeatures.csv")

## Pairwise Cosine Similarity Calculation

### Normal Parquet

In [4]:
normal_df = pd.read_parquet(
    "../data/vectorized_mp3s/pairwise_complete_parquets/20230901_complete_pairwise_data.parquet"
)
normal_df.shape

(11578, 498)

### CNN Parquet

In [5]:
cnn_df = pd.read_parquet(
    "../data/vectorized_mp3s/cnn_complete_parquets/20230901_complete_cnn_data.parquet"
)
cnn_df.shape

(11578, 1000)

### Compute Similarity

#### Normal Similarity

In [6]:
normal_similarity = pairwise.cosine_similarity(normal_df, dense_output=True)
normal_similarity

array([[1.        , 0.97973231, 0.99154322, ..., 0.98798471, 0.9864652 ,
        0.96577147],
       [0.97973231, 1.        , 0.98947364, ..., 0.98547464, 0.99003342,
        0.98766516],
       [0.99154322, 0.98947364, 1.        , ..., 0.99357991, 0.99600081,
        0.98262735],
       ...,
       [0.98798471, 0.98547464, 0.99357991, ..., 1.        , 0.99601647,
        0.98547392],
       [0.9864652 , 0.99003342, 0.99600081, ..., 0.99601647, 1.        ,
        0.9892527 ],
       [0.96577147, 0.98766516, 0.98262735, ..., 0.98547392, 0.9892527 ,
        1.        ]])

In [7]:
normal_similarity_sorted = np.argsort(normal_similarity)[:, ::-1]

In [9]:
# Randomally select 10 rows from similarity array to produce playlists
# This is the list of 10 tracks originally choosen
# [8287, 6024, 2198, 7085, 3643, 3800, 5556, 7504, 3255, 1918]
np.random.seed(123)
normal_rows = np.random.choice(11578, 10, replace=False)
normal_recommendations = []
for normal_row in normal_rows:
    vec = list(normal_similarity_sorted[normal_row, 0:11])  # selects vector from array
    recommendation_vec = list(normal_df.iloc[vec, :].index)
    normal_recommendations.append(recommendation_vec)

In [10]:
normal_rows

array([8287, 6024, 2198, 7085, 3643, 3800, 5556, 7504, 3255, 1918])

#### CNN Similarity

In [12]:
cnn_similarity = pairwise.cosine_similarity(cnn_df, dense_output=True)
cnn_similarity

array([[0.9999999 , 0.96258837, 0.99975014, ..., 0.9996804 , 0.7478662 ,
        0.8212553 ],
       [0.96258837, 0.9999997 , 0.96280265, ..., 0.9655044 , 0.7904676 ,
        0.9046931 ],
       [0.99975014, 0.96280265, 0.99999994, ..., 0.9994428 , 0.7471412 ,
        0.81841034],
       ...,
       [0.9996804 , 0.9655044 , 0.9994428 , ..., 1.        , 0.75507843,
        0.83261484],
       [0.7478662 , 0.7904676 , 0.7471412 , ..., 0.75507843, 1.0000006 ,
        0.71857   ],
       [0.8212553 , 0.9046931 , 0.81841034, ..., 0.83261484, 0.71857   ,
        0.99999964]], dtype=float32)

In [13]:
cnn_similarity_sorted = np.argsort(cnn_similarity)[:, ::-1]

In [14]:
# Randomally select 10 rows from similarity array to produce playlists
# This is the list of 10 tracks originally choosen
# [8287, 6024, 2198, 7085, 3643, 3800, 5556, 7504, 3255, 1918]
np.random.seed(123)
cnn_rows = np.random.choice(11578, 10, replace=False)
cnn_recommendations = []
for cnn_row in cnn_rows:
    vec = list(cnn_similarity_sorted[cnn_row, 0:11])  # selects vector from array
    recommendation_vec = list(cnn_df.iloc[vec, :].index)
    cnn_recommendations.append(recommendation_vec)

In [15]:
cnn_rows

array([8287, 6024, 2198, 7085, 3643, 3800, 5556, 7504, 3255, 1918])

#### Check Normal Recommendations

In [16]:
normal_recommendation_df = kaggle_df.copy(deep=True)
normal_recommendation_df["track_id"] = normal_recommendation_df["track_id"].astype(
    "category"
)
normal_recommendation_df[
    "track_id"
] = normal_recommendation_df.track_id.cat.set_categories(normal_recommendations[3])

In [17]:
normal_track_recommendations = normal_recommendation_df.copy(deep=True).sort_values(
    ["track_id"]
)  # sorts heirarchy
# track_recommendations.head()
normal_track_recommendations = normal_track_recommendations.drop_duplicates(
    subset="track_id"
)
normal_track_recommendations.head(11)

genre             artist_name  \
180270        Jazz   Green Assassin Dollar   
180055        Jazz                BluntOne   
146179        Jazz                BluntOne   
61009          R&B              The Marías   
145515        Jazz                BluntOne   
145808        Jazz                 tusken.   
25703   Electronic                   Ozoyo   
145939        Jazz                 FloFilz   
44120         Folk  Vancouver Sleep Clinic   
199078  Soundtrack           Ramin Djawadi   
177513        Jazz              Kevoe West   

                                               track_name  \
180270                                              Aware   
180055                                         Recogneyes   
146179                                   Ghost Train Haze   
61009                                            Loverboy   
145515                                         Loved Ones   
145808                                             mocean   
25703                         Where to Go (feat. Wun Two)   
145939                                          Gelbstich   
44120                                           Ayahuasca   
199078  To Vaes Dothrak - From The "Game Of Thrones" S...   
177513                                           Playdout   

                      track_id  popularity  acousticness  danceability  \
180270  2QbR9yeeX7XHznRZwsyh3F          34        0.8420         0.720   
180055  6zP7r08qkY9GIWJ7TxVV6E          35        0.7820         0.607   
146179  56ir9LGNYpV3O4U5ShDvn9          50        0.5490         0.566   
61009   3XCpEFU4uXsBq5WmVQQKC9          48        0.8080         0.651   
145515  43iOWRh6448rFtwBX6CAfZ          57        0.1630         0.811   
145808  0KFF0INOF9PT3GYWbVjfI4          56        0.7380         0.759   
25703   0fDnP59qSG3dlo1j1z1fHl          34        0.1780         0.469   
145939  7niUZWARcEMEntcEOeiTH4          55        0.5430         0.740   
44120   6oVm5ocTB8B0rjO5dZk8Px          51        0.7340         0.463   
199078  6hJA1KQ8AK2r1mazUOQWGM          41        0.7970         0.465   
177513  4pNc7TWXJb9OUbI1cd0kGM          41        0.0562         0.799   

        duration_ms  energy  instrumentalness key  liveness  loudness   mode  \
180270        73500   0.268             0.958   A    0.1420   -12.323  Minor   
180055       100043   0.354             0.855   B    0.1150    -8.413  Minor   
146179       113468   0.125             0.543   B    0.1250    -9.770  Minor   
61009         73236   0.152             0.422   G    0.1170   -18.704  Minor   
145515        99765   0.181             0.880   E    0.0861   -11.996  Minor   
145808       149318   0.225             0.843   B    0.1500   -13.165  Minor   
25703        106667   0.372             0.909  A#    0.1480   -12.275  Major   
145939       117774   0.265             0.973  C#    0.1150   -11.693  Major   
44120        508602   0.228             0.110   E    0.0691   -15.717  Minor   
199078        88867   0.254             0.897  G#    0.0946   -24.967  Major   
177513       100465   0.357             0.628  A#    0.2010   -14.053  Minor   

        speechiness    tempo time_signature  valence  
180270       0.1020   80.132          4-Apr   0.4040  
180055       0.1060   78.832          4-Apr   0.8310  
146179       0.1360  128.428          4-May   0.5240  
61009        0.0832  131.088          4-Apr   0.0746  
145515       0.4460   38.498          4-Apr   0.4690  
145808       0.1290   88.022          4-Apr   0.3850  
25703        0.3240  121.355          4-Mar   0.6670  
145939       0.0461   82.040          4-Apr   0.4120  
44120        0.0338  148.003          4-Apr   0.0528  
199078       0.0351  160.108          4-Mar   0.1150  
177513       0.1410   85.987          4-Apr   0.8720

In [23]:
vec = list(normal_similarity_sorted[7085, 0:11])
normal_similarity[7085, vec]  # similarity for first match

array([1.        , 0.99678356, 0.99594064, 0.99573878, 0.99568158,
       0.99548641, 0.99543346, 0.99539609, 0.9953861 , 0.99531449,
       0.9949721 ])

In [24]:
np.mean(normal_similarity[7085, vec])

0.996012108539831

#### Check CNN Recommendations

In [18]:
cnn_recommendation_df = kaggle_df.copy(deep=True)
cnn_recommendation_df["track_id"] = cnn_recommendation_df["track_id"].astype("category")
cnn_recommendation_df["track_id"] = cnn_recommendation_df.track_id.cat.set_categories(
    cnn_recommendations[3]
)

In [19]:
cnn_track_recommendations = cnn_recommendation_df.copy(deep=True).sort_values(
    ["track_id"]
)  # sorts heirarchy
# track_recommendations.head()
cnn_track_recommendations = cnn_track_recommendations.drop_duplicates(subset="track_id")
cnn_track_recommendations.head(11)

genre               artist_name  \
180270        Jazz     Green Assassin Dollar   
147873        Jazz                      Mujo   
205057  Soundtrack         Marc Streitenfeld   
180425        Jazz                  BluntOne   
89353      Hip-Hop              A$AP Twelvyy   
147190        Jazz                Lemongrass   
210093       World                 Brian Eno   
199145  Soundtrack              Trent Reznor   
220597       World               Entheogenic   
127720   Classical            Akira Kosemura   
133576      Reggae  Bob Marley & The Wailers   

                                               track_name  \
180270                                              Aware   
147873                           Mirror (feat. Made in M)   
205057                                              Alpha   
180425                                          Sahasrara   
89353                                            Strapped   
147190                                        Sunset Glow   
210093         Thursday Afternoon - 2005 Digital Remaster   
199145                                        Sugar Storm   
220597                                              Torah   
127720                                         Grow Apart   
133576  War / No More Trouble - Live at the Stanley Th...   

                      track_id  popularity  acousticness  danceability  \
180270  2QbR9yeeX7XHznRZwsyh3F          34        0.8420        0.7200   
147873  6qFTyyX88gmlPokNdf8h2z          44        0.5520        0.7240   
205057  3tDfBzg1VZBL3MkEm6bbIp          30        0.9690        0.1020   
180425  68huIHGDHk1kBNM0ofSUUk          36        0.4060        0.8370   
89353   3U0xbYGTtYZAUv3lEwPebJ          55        0.4590        0.7240   
147190  37R2gf2GpGrKuQffKCTzbF          49        0.7600        0.4990   
210093  4t3Yh6tKkxXrc458pNI7zZ          38        0.9760        0.0918   
199145  4ktkHx7JtPUk2D6ma7tUQ7          38        0.9680        0.2360   
220597  1IkxzTnEP1p0IYWU21qC1y          28        0.0504        0.5460   
127720  3IQOIjxF1OfeIZ9Hg5UBtN          34        0.9610        0.4470   
133576  6x8IAEZoyLlNLK76u2Dc6l          29        0.2160        0.4870   

        duration_ms  energy  instrumentalness key  liveness  loudness   mode  \
180270        73500  0.2680          0.958000   A    0.1420   -12.323  Minor   
147873        94250  0.0526          0.953000  C#    0.1080   -15.380  Major   
205057       136027  0.1500          0.950000   C    0.0688   -22.262  Major   
180425        96152  0.3760          0.864000   D    0.1100    -8.305  Major   
89353        197867  0.5340          0.000058  G#    0.1520    -8.631  Minor   
147190       279219  0.3750          0.896000   A    0.6480   -10.372  Minor   
210093      3650688  0.0569          0.884000   C    0.0842   -31.808  Major   
199145       173613  0.0347          0.885000   A    0.0836   -22.849  Minor   
220597       451373  0.6060          0.721000   B    0.6540   -11.574  Minor   
127720        80880  0.2720          0.860000   F    0.1230   -21.012  Major   
133576       363893  0.7530          0.000001  F#    0.9540    -7.581  Minor   

        speechiness    tempo time_signature  valence  
180270       0.1020   80.132          4-Apr   0.4040  
147873       0.1520   81.605          4-Apr   0.7140  
205057       0.0349   72.551          4-Apr   0.0620  
180425       0.1350   82.910          4-Apr   0.5120  
89353        0.3530   87.987          4-Apr   0.1120  
147190       0.0281   80.095          4-Apr   0.0772  
210093       0.0358   81.945          4-Mar   0.0527  
199145       0.0335   71.506          4-May   0.0732  
220597       0.0300  133.947          4-Apr   0.0972  
127720       0.0438   75.391          4-Mar   0.1200  
133576       0.2890  158.439          4-Apr   0.5970

In [25]:
vec = list(cnn_similarity_sorted[7085, 0:11])
cnn_similarity[7085, vec]  # similarity for first match

array([1.        , 0.9990518 , 0.98749137, 0.9763511 , 0.9221045 ,
       0.9151948 , 0.89406407, 0.8691619 , 0.8667479 , 0.83266383,
       0.80967844], dtype=float32)

In [27]:
np.mean(cnn_similarity[7085, vec])

0.9156826

In [46]:
from scipy.stats import spearmanr

sig_array = spearmanr(normal_similarity, cnn_similarity, axis=0)

/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/numpy/lib/function_base.py:2855: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


In [49]:
normal_df.head()

0         1         2         3         4  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.446197  0.432998  0.526217  0.585114  0.453538   
1Bk00Y8bvqKHzUTDfEH2RH  0.533089  0.496410  0.529498  0.539816  0.602047   
7x8MCsillTMQGAStE4dmW8  0.375435  0.506404  0.403135  0.446927  0.366386   
11uz9XML4cezgIT4LO9Zq7  0.561327  0.488023  0.637125  0.450111  0.357839   
63eqAbSLuqUQiT8wDOMWLF  0.484749  0.380538  0.420095  0.410116  0.317550   

                               5         6         7         8         9  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.393470  0.381640  0.472515  0.441829  0.436484   
1Bk00Y8bvqKHzUTDfEH2RH  0.531111  0.583465  0.500657  0.547362  0.595350   
7x8MCsillTMQGAStE4dmW8  0.480915  0.499774  0.416219  0.522652  0.362109   
11uz9XML4cezgIT4LO9Zq7  0.402176  0.474751  0.366066  0.320569  0.442026   
63eqAbSLuqUQiT8wDOMWLF  0.372825  0.370876  0.447128  0.441618  0.361918   

                              10        11        12        13        14  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.582131  0.429712  0.000000  0.000000  0.000000   
1Bk00Y8bvqKHzUTDfEH2RH  0.530005  0.601916  0.013502  0.008879  0.025781   
7x8MCsillTMQGAStE4dmW8  0.391583  0.318410  0.003151  0.004168  0.007821   
11uz9XML4cezgIT4LO9Zq7  0.595346  0.789375  0.008911  0.009713  0.010991   
63eqAbSLuqUQiT8wDOMWLF  0.385281  0.408907  0.003759  0.002013  0.004323   

                              15        16        17        18        19  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000000  0.000000  0.000000  0.000000  0.000000   
1Bk00Y8bvqKHzUTDfEH2RH  0.017854  0.016353  0.032633  0.033187  0.020770   
7x8MCsillTMQGAStE4dmW8  0.000650  0.000268  0.000343  0.000210  0.001007   
11uz9XML4cezgIT4LO9Zq7  0.007270  0.004633  0.004885  0.008912  0.004726   
63eqAbSLuqUQiT8wDOMWLF  0.007078  0.005656  0.004919  0.002898  0.005598   

                              20        21        22        23   24   25   26  \
track_id                                                                        
6DQzmTJnaZw4A9IynCGfrM  0.000000  0.000000  0.000000  0.000000  1.0  1.0  1.0   
1Bk00Y8bvqKHzUTDfEH2RH  0.020561  0.019715  0.021397  0.017325  1.0  1.0  1.0   
7x8MCsillTMQGAStE4dmW8  0.003574  0.000611  0.000178  0.003449  1.0  1.0  1.0   
11uz9XML4cezgIT4LO9Zq7  0.005685  0.006983  0.005052  0.003019  1.0  1.0  1.0   
63eqAbSLuqUQiT8wDOMWLF  0.001808  0.006693  0.011461  0.002518  1.0  1.0  1.0   

                         27   28   29   30   31   32   33   34   35  \
track_id                                                              
6DQzmTJnaZw4A9IynCGfrM  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0   
1Bk00Y8bvqKHzUTDfEH2RH  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0   
7x8MCsillTMQGAStE4dmW8  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0   
11uz9XML4cezgIT4LO9Zq7  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0   
63eqAbSLuqUQiT8wDOMWLF  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0   

                               36         37         38         39         40  \
track_id                                                                        
6DQzmTJnaZw4A9IynCGfrM -28.965864 -21.389360 -19.317324 -21.354130 -21.516270   
1Bk00Y8bvqKHzUTDfEH2RH -26.442589 -20.350389 -16.736059 -16.068079 -15.998079   
7x8MCsillTMQGAStE4dmW8 -27.700293 -25.555010 -27.493561 -30.544888 -27.802584   
11uz9XML4cezgIT4LO9Zq7 -35.881554 -31.713604 -28.821924 -30.741623 -28.591974   
63eqAbSLuqUQiT8wDOMWLF -39.543922 -33.366390 -29.568184 -32.599480 -33.892006   

                               41         42         43         44         45  \
track_id                                                                        
6DQzmTJnaZw4A9IynCGfrM -23.200346 -24.177885 -25.294035 -24.751333 -24.149071   
1Bk00Y8bvqKHzUTDfEH2RH

In [50]:
cnn_df.head()

0         1         2         3         4  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000033  0.000073  0.000034  0.000046  0.000038   
1Bk00Y8bvqKHzUTDfEH2RH  0.000092  0.000472  0.000130  0.000257  0.000349   
7x8MCsillTMQGAStE4dmW8  0.000007  0.000020  0.000009  0.000016  0.000019   
11uz9XML4cezgIT4LO9Zq7  0.000425  0.000524  0.000323  0.000799  0.000594   
63eqAbSLuqUQiT8wDOMWLF  0.000155  0.000305  0.000123  0.000304  0.000209   

                               5         6         7         8         9  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000055  0.000064  0.000059  0.000017  0.000049   
1Bk00Y8bvqKHzUTDfEH2RH  0.000602  0.000645  0.000100  0.000097  0.000260   
7x8MCsillTMQGAStE4dmW8  0.000028  0.000056  0.000012  0.000015  0.000035   
11uz9XML4cezgIT4LO9Zq7  0.002035  0.000453  0.000129  0.000225  0.000444   
63eqAbSLuqUQiT8wDOMWLF  0.001102  0.000286  0.000102  0.000056  0.000110   

                              10        11        12        13        14  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000018  0.000029  0.000026  0.000024  0.000016   
1Bk00Y8bvqKHzUTDfEH2RH  0.000065  0.000098  0.000097  0.000090  0.000050   
7x8MCsillTMQGAStE4dmW8  0.000013  0.000010  0.000012  0.000012  0.000008   
11uz9XML4cezgIT4LO9Zq7  0.000265  0.000142  0.000089  0.000118  0.000056   
63eqAbSLuqUQiT8wDOMWLF  0.000083  0.000070  0.000073  0.000093  0.000031   

                              15        16        17        18        19  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000047  0.000059  0.000027  0.000013  0.000028   
1Bk00Y8bvqKHzUTDfEH2RH  0.000166  0.000128  0.000106  0.000106  0.000081   
7x8MCsillTMQGAStE4dmW8  0.000022  0.000021  0.000015  0.000008  0.000011   
11uz9XML4cezgIT4LO9Zq7  0.000599  0.000420  0.000161  0.000085  0.000139   
63eqAbSLuqUQiT8wDOMWLF  0.000120  0.000108  0.000079  0.000044  0.000088   

                              20        21        22        23        24  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000032  0.000047  0.000053  0.000039  0.000015   
1Bk00Y8bvqKHzUTDfEH2RH  0.000174  0.000129  0.000132  0.000217  0.000113   
7x8MCsillTMQGAStE4dmW8  0.000015  0.000014  0.000016  0.000020  0.000015   
11uz9XML4cezgIT4LO9Zq7  0.000211  0.000297  0.000281  0.000161  0.000312   
63eqAbSLuqUQiT8wDOMWLF  0.000097  0.000112  0.000095  0.000115  0.000060   

                              25        26        27        28        29  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000043  0.000041  0.000036  0.000027  0.000084   
1Bk00Y8bvqKHzUTDfEH2RH  0.000103  0.000198  0.000095  0.000103  0.000404   
7x8MCsillTMQGAStE4dmW8  0.000013  0.000018  0.000012  0.000012  0.000019   
11uz9XML4cezgIT4LO9Zq7  0.000323  0.000564  0.000181  0.000226  0.000874   
63eqAbSLuqUQiT8wDOMWLF  0.000117  0.000312  0.000109  0.000081  0.000857   

                              30        31        32        33        34  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000063  0.000050  0.000039  0.000075  0.000028   
1Bk00Y8bvqKHzUTDfEH2RH  0.000260  0.000141  0.000156  0.000320  0.000117   
7x8MCsillTMQGAStE4dmW8  0.000043  0.000027  0.000018  0.000022  0.000011   
11uz9XML4cezgIT4LO9Zq7  0.000252  0.000222  0.000282  0.002537  0.000337   
63eqAbSLuqUQiT8wDOMWLF  0.000160  0.000142  0.000242  0.000310  0.000163   

                              35        36        37        38        39  \
track_id                                                                   
6DQzmTJnaZw4A9IynCGfrM  0.000126  0.000147  0.000026  0.000031  0.000015   
1Bk00Y8bvqKHzUTDfEH2RH  0.000551  0.000520  0.000103  0.000213  0.000076

In [51]:
spearmanr_df = pd.DataFrame(sig_array[0])

In [53]:
spearmanr_df.head()

0         1         2         3         4         5         6      \
0  1.000000  0.177852  0.830394 -0.589520  0.094962  0.510958 -0.121664   
1  0.177852  1.000000  0.420006 -0.116888  0.178144  0.485232 -0.135368   
2  0.830394  0.420006  1.000000 -0.278876  0.174800  0.837421  0.053045   
3 -0.589520 -0.116888 -0.278876  1.000000  0.194752  0.090721  0.758713   
4  0.094962  0.178144  0.174800  0.194752  1.000000  0.056133  0.299308   

      7         8         9         10        11        12        13     \
0  0.543150 -0.241021  0.042370  0.328006 -0.093459 -0.650823 -0.559891   
1 -0.073358  0.037802  0.712404  0.270424  0.540131 -0.192495  0.113654   
2  0.594225  0.013607  0.371476  0.540010  0.185449 -0.365962 -0.223434   
3  0.177211  0.830635  0.338401  0.372787  0.391181  0.962583  0.902613   
4  0.185042  0.317120  0.398840  0.584516  0.815765  0.225675  0.396548   

      14        15        16        17        18        19        20     \
0 -0.432019  0.608956 -0.521773  0.508358  0.055118 -0.176528  0.528151   
1 -0.004374  0.071246 -0.283814 -0.122238  0.526451  0.262093  0.010394   
2 -0.169306  0.590387 -0.337357  0.560342  0.356573  0.123616  0.455498   
3  0.903163  0.096132  0.859889  0.206372  0.526802  0.658837  0.073578   
4  0.428168  0.303490  0.477901  0.222689  0.431589  0.400142  0.341473   

      21        22        23        24        25        26        27     \
0  0.845303 -0.511614  0.593553  0.802551  0.225798  0.759912 -0.315844   
1  0.195493  0.218938  0.121510  0.023908  0.666629  0.366034  0.093495   
2  0.815987 -0.173807  0.584279  0.781566  0.392807  0.853714  0.010283   
3 -0.292474  0.816759  0.065518 -0.146428 -0.211500 -0.222237  0.896110   
4  0.012320  0.550620  0.468661  0.080980  0.358929 -0.019653  0.253047   

      28        29        30        31        32        33        34     \
0  0.629637  0.230783 -0.045008 -0.006225  0.856201 -0.170496  0.394334   
1  0.583961  0.914191  0.259468 -0.232552  0.219807  0.691853 -0.090464   
2  0.579035  0.440104  0.176729  0.120483  0.796417  0.160191  0.430332   
3 -0.719700 -0.240772  0.553557  0.673545 -0.342091  0.429746  0.328797   
4  0.007978  0.078217  0.664708  0.370631  0.110545  0.353777  0.316200   

      35        36        37        38        39        40        41     \
0  0.618926  0.481862  0.318915  0.875149  0.275765  0.808740  0.615312   
1  0.623579  0.812919  0.670609  0.458649  0.775906  0.439434  0.243766   
2  0.618593  0.717062  0.449879  0.918001  0.550783  0.804805  0.791249   
3 -0.483423 -0.094252 -0.011115 -0.498502  0.111353 -0.410882  0.047157   
4 -0.050981  0.195540  0.541688  0.057387  0.549133  0.220126  0.231427   

      42        43        44        45        46        47        48     \
0  0.694925  0.845354 -0.358591  0.563952  0.334524  0.074124  0.130678   
1  0.323059  0.231160  0.388877  0.213593  0.019134  0.624933  0.769469   
2  0.673632  0.886876  0.009582  0.700677  0.510370  0.497125  0.267007   
3 -0.115681 -0.303824  0.762091  0.088224  0.411180  0.414649 -0.150047   
4  0.475642  0.049822  0.423154  0.144387  0.062231  0.304383  0.450140   

      49        50        51        52        53        54        55     \
0  0.068562 -0.285359 -0.252754  0.079395  0.633520  0.771912  0.849056   
1  0.109457 -0.170092  0.041962  0.600284  0.564218  0.029243  0.472378   
2  0.407521 -0.130916  0.042359  0.243700  0.775533  0.646684  0.935885   
3  0.636591  0.767783  0.849533  0.090030 -0.124682 -0.178682 -0.405098   
4  0.106908  0.440728  0.271812  0.721092  0.509072  0.289996 -0.028145   

      56        57        58        59        60        61        62     \
0  0.650452  0.733352  0.747434  0.193697  0.256769  0.586586 -0.078232   
1  0.032869  0.676973  0.651480  0.743785  0.439977  0.165403 -0.226790   
2  0.745559  0.853181  0.706015  0.390200  0.551600  0.578356  0.057868   
3  0.081240 -0.471593 -0.495117  0.057298  0.320313 -0.015185  0.728383   
4  0.157538 -0.028847  